In [1]:
from numpy import sort
import vectorbt as vbt
import pandas as pd 
import datetime, pytz
from datetime import datetime, timedelta

# Read In Data

In [2]:
# Enter your parameters here

start_date = datetime(2018, 1, 1, tzinfo=pytz.utc)  # time period for analysis, must be timezone-aware
# end_date = datetime.now(pytz.utc)
# end_date = datetime(2020, 1, 1, tzinfo=pytz.utc)
# The following is the number of days to look back for the analysis
# time_buffer = timedelta(days=100)  # buffer before to pre-calculate SMA/EMA, best to set to max window


vbt.settings.portfolio['init_cash'] = 100_000.  # 100,000$
# vbt.settings.portfolio['fees'] = 0.0025  # 0.25% # These may already be incorporated into trade file 
# vbt.settings.portfolio['commission'] = 0.0025  # 0.25% May want to use this later

# Read in the Trade File from Tradingview Strategy

In [3]:
# Download trade file from tradingview strategy as csv
trade_file = "./data/Dynamic_Wavebased_1.0_Strategy_2022-02-06 (2).csv" 
df_trades = pd.read_csv(trade_file)

In [4]:
# get binance data doing it this way allows for you to update your data rather than re-downloading it
symbol = "ETHUSDT"
freq = '2h' # My strategy was based on 2hour candles for ETHUSDT
binance_data = vbt.BinanceData.download(symbol, start=start_date, end="now UTC", interval=freq, show_progress=True) 
try: 
    binance_data.load("./data/BINANCE_ETHUSDT_2h.pickle")
    print("Loaded data from file")
except: 
    print("loading data from pickle failed")
    binance_data.get() # get data from binance first time can comment this out if you want to use the data from the csv
    binance_data.save("./data/BINANCE_ETHUSDT_2h.pickle") # save data to file this is a pickle file 
# binance_data.update() # update the data
df_data = binance_data.data["ETHUSDT"] # get the dataframe from the binance data object



2018-01-01 00:00:00+00:00 - 2022-02-07 16:00:00+00:00: : 36it [00:27,  1.31it/s]

Loaded data from file


In [7]:
# If you would like to update the data, you can do it here
binance_data.update(show_progress=True)
print("Updated data")
binance_data.save("./data/BINANCE_ETHUSDT_2h.pickle")
print("Saved data")

2022-02-07 16:00:00+00:00 - 2022-02-07 16:00:00+00:00: : 1it [00:00,  1.28it/s]

Updated data
Saved data


# Fix up the tradingview trade dataframe

In [8]:
df_data.index = df_data.index.tz_convert(None) # convert the index to tz-naive
# The following only needs to be done once after reading the trades in from tradingview
df_trades = df_trades.set_index('Date/Time')
df_trades.index = pd.to_datetime(df_trades.index)


In [9]:
# combine data and trades 

df_combined  = pd.concat([df_data, df_trades]).sort_index()
df_combined = df_combined[["Close", "Type"]]

In [10]:
# This creates the boolean for the signals
df_combined["entries"] = df_combined["Type"] == "Entry Long"
df_combined["exits"] = df_combined["Type"] == "Exit Long"
df_combined["short_entries"] = df_combined["Type"] == "Entry Short"
df_combined["short_exits"] = df_combined["Type"] == "Exit Short"
print(df_combined)

                       Close Type  entries  exits  short_entries  short_exits
2018-01-01 00:00:00   717.97  NaN    False  False          False        False
2018-01-01 02:00:00   734.50  NaN    False  False          False        False
2018-01-01 04:00:00   748.99  NaN    False  False          False        False
2018-01-01 06:00:00   751.99  NaN    False  False          False        False
2018-01-01 08:00:00   753.21  NaN    False  False          False        False
...                      ...  ...      ...    ...            ...          ...
2022-02-07 08:00:00  3067.06  NaN    False  False          False        False
2022-02-07 10:00:00  3067.24  NaN    False  False          False        False
2022-02-07 12:00:00  3088.89  NaN    False  False          False        False
2022-02-07 14:00:00  3123.15  NaN    False  False          False        False
2022-02-07 16:00:00  3122.22  NaN    False  False          False        False

[19196 rows x 6 columns]


In [24]:
# Show the Long and Short signals
print(df_combined["entries"].value_counts())
print(df_combined["short_entries"].value_counts())


False    18887
True       309
Name: entries, dtype: int64
False    18875
True       321
Name: short_entries, dtype: int64


In [11]:
# Create the portfolio object

portfolio = vbt.Portfolio.from_signals(df_combined["Close"], 
                                        entries=df_combined["entries"].to_list(), 
                                        exits=df_combined["exits"].to_list(), 
                                        short_entries=df_combined["short_entries"].to_list(), 
                                        short_exits=df_combined["short_exits"].to_list(), 
                                        price=df_combined['Close'].vbt.fshift(1),
                                        )

In [12]:
# Show the positions and trades in a readable format
print(portfolio.positions.records_readable)

     Position Id Column        Size     Entry Timestamp  Avg Entry Price  \
0              0  Close  133.547009 2018-01-01 16:00:00           748.80   
1              1  Close  134.466875 2018-01-01 20:00:00           746.23   
2              2  Close  108.237656 2018-01-26 18:00:00          1061.31   
3              3  Close  128.577570 2018-02-16 10:00:00           921.78   
4              4  Close  141.731578 2018-02-25 16:00:00           823.33   
..           ...    ...         ...                 ...              ...   
435          435  Close  246.603799 2022-01-24 00:00:00          2539.01   
436          436  Close  246.603799 2022-01-24 08:00:00          2386.65   
437          437  Close  244.165935 2022-01-30 20:00:00          2560.25   
438          438  Close  244.517142 2022-01-31 14:00:00          2558.41   
439          439  Close  240.548178 2022-02-02 16:00:00          2663.90   

     Entry Fees      Exit Timestamp  Avg Exit Price  Exit Fees           PnL  \
0      

In [20]:
portfolio.positions.records_readable.columns

Index(['Position Id', 'Column', 'Size', 'Entry Timestamp', 'Avg Entry Price',
       'Entry Fees', 'Exit Timestamp', 'Avg Exit Price', 'Exit Fees', 'PnL',
       'Return', 'Direction', 'Status'],
      dtype='object')

In [21]:
# Check the vectorbt portfolio trades 
portfolio.positions.records_readable["Direction"].value_counts()

Short    223
Long     217
Name: Direction, dtype: int64

In [25]:
# Show the Long and Short signals
print(df_combined["entries"].value_counts())
print(df_combined["short_entries"].value_counts())

False    18887
True       309
Name: entries, dtype: int64
False    18875
True       321
Name: short_entries, dtype: int64


# Let's look at the results from VectorBT

In [27]:
df_combined

Close Type  entries  exits  short_entries  short_exits
2018-01-01 00:00:00   717.97  NaN    False  False          False        False
2018-01-01 02:00:00   734.50  NaN    False  False          False        False
2018-01-01 04:00:00   748.99  NaN    False  False          False        False
2018-01-01 06:00:00   751.99  NaN    False  False          False        False
2018-01-01 08:00:00   753.21  NaN    False  False          False        False
...                      ...  ...      ...    ...            ...          ...
2022-02-07 08:00:00  3067.06  NaN    False  False          False        False
2022-02-07 10:00:00  3067.24  NaN    False  False          False        False
2022-02-07 12:00:00  3088.89  NaN    False  False          False        False
2022-02-07 14:00:00  3123.15  NaN    False  False          False        False
2022-02-07 16:00:00  3122.22  NaN    False  False          False        False

[19196 rows x 6 columns]

In [32]:
# Show the portfolio statistics and compare the returns of the banchmark
bm_rets = df_combined["Close"].vbt.to_returns() # create returns dataframe for the benchmark
portfolio.stats(settings=dict(benchmark_returns=bm_rets, # Sets the benchmark returns for stats comparisons
                              frequency='2h', # Sets the frequency for stats comparisons
                              )
                )

Start                         2018-01-01 00:00:00
End                           2022-02-07 16:00:00
Period                                      19196
Start Value                              100000.0
End Value                           641741.646906
Total Return [%]                       541.741647
Benchmark Return [%]                   334.867752
Max Gross Exposure [%]                      100.0
Total Fees Paid                               0.0
Max Drawdown [%]                        33.514544
Max Drawdown Duration                      4368.0
Total Trades                                  440
Total Closed Trades                           440
Total Open Trades                               0
Open Trade PnL                                0.0
Win Rate [%]                            51.136364
Best Trade [%]                           14.48079
Worst Trade [%]                        -18.078352
Avg Winning Trade [%]                    2.845104
Avg Losing Trade [%]                    -2.006068


In [28]:
portfolio.stats()
portfolio.plot().show()

/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning: Metric 'sharpe_ratio' requires frequency to be set
  warnings.warn(warning_message)
/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning: Metric 'calmar_ratio' requires frequency to be set
  warnings.warn(warning_message)
/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning: Metric 'omega_ratio' requires frequency to be set
  warnings.warn(warning_message)
/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning: Metric 'sortino_ratio' requires frequency to be set
  warnings.warn(warning_message)
